In [1]:
import os
import pandas as pd
import altair as alt
import numpy as np
from vega_datasets import data
from altair.expr import datum, geoCentroid

In [2]:
root = '/Users/cynthiaxu/Documents/MIDS/03_2023 Fall/209 Data Visualization/209-ds-salaries-viz-project/'
folder = 'data'

data_path = os.path.join(root, folder)
data_path

'/Users/cynthiaxu/Documents/MIDS/03_2023 Fall/209 Data Visualization/209-ds-salaries-viz-project/data'

In [3]:
data_files = os.listdir(data_path)
data_files = [file for file in data_files if '2021' in file and '.csv' in file]
data_files

['Data Science Salary 2021 to 2023.csv', 'data_cleaned_2021.csv']

In [4]:
sal_df = pd.read_csv(os.path.join(data_path, data_files[0]))
skill_df = pd.read_csv(os.path.join(data_path, data_files[1]))

In [5]:
sal_df

work_year experience_level employment_type                  job_title  \
0          2023               EN              FT          Applied Scientist   
1          2023               EN              FT          Applied Scientist   
2          2023               EN              FT       Data Quality Analyst   
3          2023               EN              FT    Compliance Data Analyst   
4          2023               EN              FT          Applied Scientist   
...         ...              ...             ...                        ...   
3756       2020               SE              FT   Principal Data Scientist   
3757       2020               SE              FT             Data Scientist   
3758       2020               SE              FT       Data Science Manager   
3759       2020               SE              FT  Machine Learning Engineer   
3760       2020               SE              FT             Data Scientist   

      salary salary_currency  salary_in_usd company_location company_size  
0     213660             USD         213660               US            L  
1     130760             USD         130760               US            L  
2     100000             USD         100000               NG            L  
3      30000             USD          30000               NG            L  
4     204620             USD         204620               US            L  
...      ...             ...            ...              ...          ...  
3756  130000             EUR         148261               DE            M  
3757   80000             EUR          91237               AT            S  
3758  190200             USD         190200               US            M  
3759   40000             EUR          45618               HR            S  
3760  412000             USD         412000               US            L  

[3761 rows x 9 columns]

In [6]:
geo_file = [file for file in os.listdir(data_path) if 'countries' in file]

geo_df = pd.read_csv(os.path.join(data_path, geo_file[0]))
for i, col in enumerate(geo_df.columns):
    geo_df.iloc[:, i] = geo_df.iloc[:, i].str.replace('"', '')

geo_df['Alpha-2 code'] = geo_df['Alpha-2 code'].apply(lambda x: x.replace(' ', ''))

geo_df['Alpha-2 code'] = geo_df['Alpha-2 code'].astype(str)
geo_df['Latitude (average)'] = geo_df['Latitude (average)'].astype(float)
geo_df['Longitude (average)'] = geo_df['Longitude (average)'].astype(float)
geo_df

Country Alpha-2 code Alpha-3 code Numeric code  \
0          Afghanistan           AF          AFG            4   
1              Albania           AL          ALB            8   
2              Algeria           DZ          DZA           12   
3       American Samoa           AS          ASM           16   
4              Andorra           AD          AND           20   
..                 ...          ...          ...          ...   
251  Wallis and Futuna           WF          WLF          876   
252     Western Sahara           EH          ESH          732   
253              Yemen           YE          YEM          887   
254             Zambia           ZM          ZMB          894   
255           Zimbabwe           ZW          ZWE          716   

     Latitude (average)  Longitude (average)  
0               33.0000                 65.0  
1               41.0000                 20.0  
2               28.0000                  3.0  
3              -14.3333               -170.0  
4               42.5000                  1.6  
..                  ...                  ...  
251            -13.3000               -176.2  
252             24.5000                -13.0  
253             15.0000                 48.0  
254            -15.0000                 30.0  
255            -20.0000                 30.0  

[256 rows x 6 columns]

In [7]:
df = sal_df.merge(geo_df, left_on=['company_location'], right_on=['Alpha-2 code'], how='left')
df

work_year experience_level employment_type                  job_title  \
0          2023               EN              FT          Applied Scientist   
1          2023               EN              FT          Applied Scientist   
2          2023               EN              FT       Data Quality Analyst   
3          2023               EN              FT    Compliance Data Analyst   
4          2023               EN              FT          Applied Scientist   
...         ...              ...             ...                        ...   
3761       2020               SE              FT   Principal Data Scientist   
3762       2020               SE              FT             Data Scientist   
3763       2020               SE              FT       Data Science Manager   
3764       2020               SE              FT  Machine Learning Engineer   
3765       2020               SE              FT             Data Scientist   

      salary salary_currency  salary_in_usd company_location company_size  \
0     213660             USD         213660               US            L   
1     130760             USD         130760               US            L   
2     100000             USD         100000               NG            L   
3      30000             USD          30000               NG            L   
4     204620             USD         204620               US            L   
...      ...             ...            ...              ...          ...   
3761  130000             EUR         148261               DE            M   
3762   80000             EUR          91237               AT            S   
3763  190200             USD         190200               US            M   
3764   40000             EUR          45618               HR            S   
3765  412000             USD         412000               US            L   

            Country Alpha-2 code Alpha-3 code Numeric code  \
0     United States           US          USA          840   
1     United States           US          USA          840   
2           Nigeria           NG          NGA          566   
3           Nigeria           NG          NGA          566   
4     United States           US          USA          840   
...             ...          ...          ...          ...   
3761        Germany           DE          DEU          276   
3762        Austria           AT          AUT           40   
3763  United States           US          USA          840   
3764        Croatia           HR          HRV          191   
3765  United States           US          USA          840   

      Latitude (average)  Longitude (average)  
0                38.0000             -97.0000  
1                38.0000             -97.0000  
2                10.0000               8.0000  
3                10.0000               8.0000  
4                38.0000             -97.0000  
...                  ...                  ...  
3761             51.0000               9.0000  
3762             47.3333              13.3333  
3763             38.0000             -97.0000  
3764             45.1667              15.5000  
3765             38.0000             -97.0000  

[3766 rows x 15 columns]

In [20]:
#jitter points
sigma = 4
df['latitude'] = df['Latitude (average)'].apply(lambda x: np.random.normal(x, sigma, 1)).astype(float)
df['longitude'] = df['Longitude (average)'].apply(lambda x: np.random.normal(x, sigma, 1)).astype(float)
df

work_year experience_level employment_type                  job_title  \
0          2023               EN              FT          Applied Scientist   
1          2023               EN              FT          Applied Scientist   
2          2023               EN              FT       Data Quality Analyst   
3          2023               EN              FT    Compliance Data Analyst   
4          2023               EN              FT          Applied Scientist   
...         ...              ...             ...                        ...   
3761       2020               SE              FT   Principal Data Scientist   
3762       2020               SE              FT             Data Scientist   
3763       2020               SE              FT       Data Science Manager   
3764       2020               SE              FT  Machine Learning Engineer   
3765       2020               SE              FT             Data Scientist   

      salary salary_currency  salary_in_usd company_location company_size  \
0     213660             USD         213660               US            L   
1     130760             USD         130760               US            L   
2     100000             USD         100000               NG            L   
3      30000             USD          30000               NG            L   
4     204620             USD         204620               US            L   
...      ...             ...            ...              ...          ...   
3761  130000             EUR         148261               DE            M   
3762   80000             EUR          91237               AT            S   
3763  190200             USD         190200               US            M   
3764   40000             EUR          45618               HR            S   
3765  412000             USD         412000               US            L   

            Country Alpha-2 code Alpha-3 code Numeric code  \
0     United States           US          USA          840   
1     United States           US          USA          840   
2           Nigeria           NG          NGA          566   
3           Nigeria           NG          NGA          566   
4     United States           US          USA          840   
...             ...          ...          ...          ...   
3761        Germany           DE          DEU          276   
3762        Austria           AT          AUT           40   
3763  United States           US          USA          840   
3764        Croatia           HR          HRV          191   
3765  United States           US          USA          840   

      Latitude (average)  Longitude (average)   latitude   longitude  
0                38.0000             -97.0000  43.337158  -89.559866  
1                38.0000             -97.0000  40.183000 -100.751355  
2                10.0000               8.0000   6.058984   13.509799  
3                10.0000               8.0000  14.375458    8.514062  
4                38.0000             -97.0000  36.009631  -97.165833  
...                  ...                  ...        ...         ...  
3761             51.0000               9.0000  55.236163    5.899388  
3762             47.3333              13.3333  51.381410   12.807165  
3763             38.0000             -97.0000  39.138247  -98.382419  
3764             45.1667              15.5000  41.986972   17.497009  
3765             38.0000             -97.0000  41.048582  -98.541839  

[3766 rows x 17 columns]

In [9]:
#iteration 1
countries = alt.topo_feature(data.world_110m.url, 'countries')

background = alt.Chart(countries).mark_geoshape(
    fill='lightgray',
    stroke='white'
).project(
    "equirectangular"
).properties(
    width=800,
    height=400
)

points = alt.Chart(df, title = 'Location of Data Science Roles').mark_circle().encode(
    longitude='longitude:Q',
    latitude='latitude:Q',
    size=alt.value(10)
    # tooltip='name'
)

iter1 = background + points
iter1.save(os.path.join(root, 'images', 'iteration1.html'))
iter1

/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_n

alt.LayerChart(...)

In [10]:
#iteration 2
#try with bubbles to represent average salaries
background = alt.Chart(countries).mark_geoshape(
    fill='lightgray',
    stroke='white'
).project(
    "equirectangular"
).properties(
    width=800,
    height=400
)

bubbles = alt.Chart(df, title = 'Location of Data Science Roles').transform_calculate(
    centroid=geoCentroid(None, datum)
).mark_circle(
    stroke='navy'
).encode(
    longitude='longitude:Q',
    latitude='latitude:Q',
    size="median(salary_in_usd)"
)

iter2 = background + bubbles
iter2.save(os.path.join(root, 'images', 'iteration2.html'))
iter2

/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_n

alt.LayerChart(...)

In [51]:
#iteration 3
#try a choropleth
world_map_data = alt.topo_feature('https://vega.github.io/vega-datasets/data/world-110m.json', 'countries')
background = alt.Chart(countries).mark_geoshape(
    fill='lightgray',
    stroke='white'
).project(
    "equirectangular"
).properties(
    width=500,
    height=300
)

choro = alt.Chart(df).mark_geoshape().encode(
    alt.Color('median(salary_in_usd)', scale=alt.Scale(scheme='viridis')),
    tooltip=['Country:N', 'median(salary_in_usd)']
).project(
    "equirectangular"
).properties(
    width=500,
    height=300,
    title='Median Salary by Country'
)

background + choro

/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_n

alt.LayerChart(...)

In [63]:
merged_data

work_year experience_level employment_type                  job_title  \
0          2023               EN              FT          Applied Scientist   
1          2023               EN              FT          Applied Scientist   
2          2023               EN              FT       Data Quality Analyst   
3          2023               EN              FT    Compliance Data Analyst   
4          2023               EN              FT          Applied Scientist   
...         ...              ...             ...                        ...   
3761       2020               SE              FT   Principal Data Scientist   
3762       2020               SE              FT             Data Scientist   
3763       2020               SE              FT       Data Science Manager   
3764       2020               SE              FT  Machine Learning Engineer   
3765       2020               SE              FT             Data Scientist   

      salary salary_currency  salary_in_usd company_location company_size  \
0     213660             USD         213660               US            L   
1     130760             USD         130760               US            L   
2     100000             USD         100000               NG            L   
3      30000             USD          30000               NG            L   
4     204620             USD         204620               US            L   
...      ...             ...            ...              ...          ...   
3761  130000             EUR         148261               DE            M   
3762   80000             EUR          91237               AT            S   
3763  190200             USD         190200               US            M   
3764   40000             EUR          45618               HR            S   
3765  412000             USD         412000               US            L   

            Country  ... Latitude (average) Longitude (average)   latitude  \
0     United States  ...            38.0000            -97.0000  34.720548   
1     United States  ...            38.0000            -97.0000  41.843178   
2           Nigeria  ...            10.0000              8.0000        NaN   
3           Nigeria  ...            10.0000              8.0000        NaN   
4     United States  ...            38.0000            -97.0000  41.303638   
...             ...  ...                ...                 ...        ...   
3761        Germany  ...            51.0000              9.0000        NaN   
3762        Austria  ...            47.3333             13.3333        NaN   
3763  United States  ...            38.0000            -97.0000  37.213727   
3764        Croatia  ...            45.1667             15.5000        NaN   
3765  United States  ...            38.0000            -97.0000  37.502023   

       longitude  pop_est  continent  name  iso_a3 gdp_md_est geometry  
0    -100.997446      NaN        NaN   NaN     NaN        NaN     None  
1     -99.214428      NaN        NaN   NaN     NaN        NaN     None  
2            NaN      NaN        NaN   NaN     NaN        NaN     None  
3            NaN      NaN        NaN   NaN     NaN        NaN     None  
4     -96.549417      NaN        NaN   NaN     NaN        NaN     None  
...          ...      ...        ...   ...     ...        ...      ...  
3761         NaN      NaN        NaN   NaN     NaN        NaN     None  
3762         NaN      NaN        NaN   NaN     NaN        NaN     None  
3763  -99.214986      NaN        NaN   NaN     NaN        NaN     None  
3764         NaN      NaN        NaN   NaN     NaN        NaN     None  
3765 -106.798850      NaN        NaN   NaN     NaN        NaN     None  

[3766 rows x 23 columns]

In [64]:
world

pop_est      continent                      name iso_a3  gdp_md_est  \
0       889953.0        Oceania                      Fiji    FJI        5496   
1     58005463.0         Africa                  Tanzania    TZA       63177   
2       603253.0         Africa                 W. Sahara    ESH         907   
3     37589262.0  North America                    Canada    CAN     1736425   
4    328239523.0  North America  United States of America    USA    21433226   
..           ...            ...                       ...    ...         ...   
172    6944975.0         Europe                    Serbia    SRB       51475   
173     622137.0         Europe                Montenegro    MNE        5542   
174    1794248.0         Europe                    Kosovo    -99        7926   
175    1394973.0  North America       Trinidad and Tobago    TTO       24269   
176   11062113.0         Africa                  S. Sudan    SSD       11998   

                                              geometry  
0    MULTIPOLYGON (((180.00000 -16.06713, 180.00000...  
1    POLYGON ((33.90371 -0.95000, 34.07262 -1.05982...  
2    POLYGON ((-8.66559 27.65643, -8.66512 27.58948...  
3    MULTIPOLYGON (((-122.84000 49.00000, -122.9742...  
4    MULTIPOLYGON (((-122.84000 49.00000, -120.0000...  
..                                                 ...  
172  POLYGON ((18.82982 45.90887, 18.82984 45.90888...  
173  POLYGON ((20.07070 42.58863, 19.80161 42.50009...  
174  POLYGON ((20.59025 41.85541, 20.52295 42.21787...  
175  POLYGON ((-61.68000 10.76000, -61.10500 10.890...  
176  POLYGON ((30.83385 3.50917, 29.95350 4.17370, ...  

[177 rows x 6 columns]

In [65]:
df.to_csv(os.path.join(root, 'data', 'salary_with_GPS.csv'))

In [62]:
import geopandas as gpd
import altair as alt

# Load world country boundaries data
world = gpd.read_file(gpd.datasets.get_path('naturalearth_lowres'))

# Assuming you have a DataFrame df with 'Country' and 'median(salary_in_usd)' columns

# Merge your salary data with world country boundaries using a common identifier (e.g., 'Country')
merged_data = df.merge(world, right_on='iso_a3', left_on='Alpha-3 code', how='left')

# Create a choropleth map
choropleth_map = alt.Chart(alt.Data(values=merged_data)).mark_geoshape().encode(
    color=alt.Color('median(salary_in_usd):Q', scale=alt.Scale(scheme='viridis')),
    tooltip=['name:N', 'median(salary_in_usd):Q']
).project(
    'equirectangular'
).properties(
    width=800,
    height=400,
    title='Median Salary by Country'
)

choropleth_map


/var/folders/t7/9qpt6ghx7x132zp3932q2fb80000gn/T/ipykernel_17795/3378271882.py:5: FutureWarning: The geopandas.dataset module is deprecated and will be removed in GeoPandas 1.0. You can get the original 'naturalearth_lowres' data from https://www.naturalearthdata.com/downloads/110m-cultural-vectors/.
  world = gpd.read_file(gpd.datasets.get_path('naturalearth_lowres'))


alt.Chart(...)